In [90]:
import os, sys
import shutil
import scipy.io as scio 
import sys
import yaml
import shutil
import numpy as np
import pandas as pd
from random import shuffle
import random

def read_config(config_path='./config/config.yaml'):
    file = open(config_path, 'r', encoding="utf-8")
    #读取文件中的所有数据
    file_data = file.read()                 
    file.close()
    #指定Loader
    config_data = yaml.load(file_data,Loader=yaml.FullLoader)    
    return config_data

class convert_datasets:
    def __init__(self,config_data):
        np.set_printoptions(linewidth=1000)#防止numpy转换str自动换行    
        self.output_path = os.path.join(config_data['output_path'],config_data['output_floder_name'])

        #self.data_info_path=os.path.join(config_data['root_path'],config_data['data_info'])
        #self.data_info=read_config(data_info_path)
        self.source_image_path=os.path.join(config_data['root_path'],config_data['image_floder'])
        self.source_velodyne_path=os.path.join(config_data['root_path'],config_data['velodyne_floder'])
        self.source_calib_path=os.path.join(config_data['root_path'],config_data['calib_floder'])
        self.source_camera_Tr_path=os.path.join(config_data['root_path'],config_data['lidar_to_camera_floder'])
        self.source_camera_label=os.path.join(config_data['root_path'],config_data['camera_label_floder'])
        self.source_velodyne_label=os.path.join(config_data['root_path'],config_data['virtuallidar_label_floder'])

        self.calib_path=os.path.join(self.output_path,"calib")
        self.image2_path=os.path.join(self.output_path,"image_2")
        self.label2_path=os.path.join(self.output_path,"label_2")
        self.label_vel_path=os.path.join(self.output_path,"label_velodyne")
        self.velodyne_path=os.path.join(self.output_path,"velodyne")
        self.splitting_path=os.path.join(self.output_path,"splitting")
        
        self.train_set_proportion=config_data['train_set_proportion']
        self.validation_set_proportion=config_data['validation_set_proportion']
        self.test_set_proportion=config_data['test_set_proportion']
        self.random_seed=config_data['random_seed']
        self.onlyFileName=config_data['onlyFileName']
        
        self.create_floders_list=[]
        self.create_floders_list.append(self.calib_path)
        #self.create_floders_list.append(self.image2_path)
        self.create_floders_list.append(self.label2_path)
        self.create_floders_list.append(self.label_vel_path)
        self.create_floders_list.append(self.splitting_path)        
        
        #self.create_floders_list.append(self.velodyne_path)
        #print("create_floders list:",self.create_floders_list)
        
        #self.files_list = os.listdir(self.source_image_path)
        #self.files_list.sort()
        #self.files_len=len(self.files_list)
        self.car_count=0
        self.van_count=0

    #创建目录，返回路径
    def create_path(self):
        for floder in self.create_floders_list:        
            if not os.path.exists(floder):
                os.makedirs(floder)
                print("created the path:",floder)

    def check_files(self):
        #check image, velodyne and label are correspond.
        pass

    def calib_convert(self):
        output_path=self.calib_path
        calib_input_path=self.source_calib_path
        tr_input_path=self.source_camera_Tr_path
        
        self.calib_list = os.listdir(self.source_calib_path)
        self.calib_list.sort()          #no neceressory, save time
        for index in self.calib_list:
            calib=read_config(os.path.join(calib_input_path,index))
            tr=read_config(os.path.join(tr_input_path,index))

            rotation_matrix=np.mat(tr["rotation"])
            translation_matrix=np.mat(tr["translation"])
            Tr_matrix=np.c_[rotation_matrix,translation_matrix]          
            Tr_matrix=Tr_matrix.flatten()
            Tr_matrix=str(Tr_matrix)
            Tr_matrix=Tr_matrix.strip("[]")#delete "[" and "]"
            Tr_matrix=Tr_matrix.replace("  "," ")# replace the "," to " "
            #matrix="P2: "+matrix
            Tr_matrix="Tr_velo_to_cam: "+Tr_matrix
            #print(index,Tr_matrix)
            
            #P2_matrix=str(calib["P"])#not P matrix
            P2_matrix=str(calib["cam_K"])# should use cam_K matrix
            P2_matrix=P2_matrix.strip("[]")
            P2_matrix=P2_matrix.replace(",","")# replace the "," to " "
            P2_matrix="P2: "+P2_matrix

            output_name = os.path.splitext(index)
            with open(os.path.join(output_path,output_name[0]+".txt"), 'wt') as f:
                print("write file:",os.path.join(output_path,output_name[0]+".txt"))
                f.write("P0: \n")
                f.write("P1: \n")
                f.write(P2_matrix+"\n")
                f.write("P3: \n")
                f.write("R0_rect: \n")
                f.write(Tr_matrix)

             
                            
    def label_convert(self,input_path,output_path):
        files_list = os.listdir(input_path)
        files_list.sort()
        #print(files_list)
        
        for index in files_list:
            label=read_config(os.path.join(input_path,index))
            output_name = os.path.splitext(index)
            with open(os.path.join(output_path,output_name[0]+".txt"), 'wt') as f:
                print("write file:",os.path.join(output_path,output_name[0]+".txt"))
                for line in label:
                    #print("line: ",line,"\n")
                    f.write(line['type']+" ")
                    f.write(line['truncated_state']+" ")
                    f.write(line['occluded_state']+" ")
                    f.write(line['alpha']+" ")
                    f.write(line['2d_box']['xmin']+" ")
                    f.write(line['2d_box']['ymin']+" ")
                    f.write(line['2d_box']['xmax']+" ")
                    f.write(line['2d_box']['ymax']+" ")

                    f.write(line['3d_dimensions']['h']+" ")
                    f.write(line['3d_dimensions']['w']+" ")
                    f.write(line['3d_dimensions']['l']+" ")

                    f.write(line['3d_location']['x']+" ")
                    f.write(line['3d_location']['y']+" ")
                    f.write(line['3d_location']['z']+" ")

                    f.write(line['rotation']+" "+"\n")
    def label_convert_fix_high(self,camera_label_path,lidar_label_path,output_path):
        delete_class=['Trafficcone','Motorcyclist','Cyclist']#Set the list you want to delete
        merge_class={'Car':['Van']}#Set the list you want to merge,example 'a':[1, 2, 3],'b':[13, 22, 32],'c':[15, 'sdf']


        '''
        for key,value in merge_class.items():
            print(key,value)    
        '''

        lidar_files_list = os.listdir(lidar_label_path)
        lidar_files_list.sort()
        camera_files_list = os.listdir(camera_label_path)
        camera_files_list.sort()        
        #print(files_list)
        self.car_count=0
        self.van_count=0
        
        for index in lidar_files_list:
            lidar_label=read_config(os.path.join(lidar_label_path,index))
            camera_label=read_config(os.path.join(camera_label_path,index))
                        
            output_name = os.path.splitext(index)
            with open(os.path.join(output_path,output_name[0]+".txt"), 'wt') as f:
                print("write file:",os.path.join(output_path,output_name[0]+".txt"))
                write_buffer=""
                for camera_line,lidar_line in zip(camera_label,lidar_label):

                    if camera_line['type'] in delete_class:
                        #print("Skip the class",camera_line['type'])
                        pass
                    else:
                        for key,value in merge_class.items(): 
                            if camera_line['type'] in value:
                                print("replace the class",camera_line['type'], "to",key)
                                camera_line['type']=key

                        

                        if camera_line['type']=="Car":
                            self.car_count=self.car_count+1
                        elif camera_line['type']=="Van":
                            self.van_count=self.van_count+1
                        write_buffer+=camera_line['type']+" "
                        write_buffer+=camera_line['truncated_state']+" "
                        write_buffer+=camera_line['occluded_state']+" "
                        write_buffer+=camera_line['alpha']+" "
                        write_buffer+=camera_line['2d_box']['xmin']+" "
                        write_buffer+=camera_line['2d_box']['ymin']+" "
                        write_buffer+=camera_line['2d_box']['xmax']+" "
                        write_buffer+=camera_line['2d_box']['ymax']+" "

                        write_buffer+=lidar_line['3d_dimensions']['h']+" "
                        write_buffer+=lidar_line['3d_dimensions']['w']+" "
                        write_buffer+=lidar_line['3d_dimensions']['l']+" "

                        write_buffer+=camera_line['3d_location']['x']+" "
                        write_buffer+=camera_line['3d_location']['y']+" "
                        write_buffer+=lidar_line['3d_location']['z']+" "

                        write_buffer+=camera_line['rotation']+" "+"\n"
                        #print("write_buffer:",write_buffer)
                f.write(write_buffer)
        print("car_count",self.car_count)
        print("van_count",self.van_count)
                    
    def rename_floder(self,input_path,output_path):
        print("copy file from ",input_path,"to the ",output_path)
        shutil.copytree(input_path,output_path)
        
    def creat_list(self):
        
        random_seed=self.random_seed
        onlyFileName=self.onlyFileName
        random.seed(int(random_seed))
        r=random.random()
        
        output_path=self.splitting_path
        print("datasets splitting output path: ",output_path)
        camera_files_list = os.listdir(self.image2_path)
        #random.shuffle(camera_files_list,random=r)#打乱list
        shuffle(camera_files_list)#打乱list
        #camera_files_list.sort()        
        #print("camera_list: ",camera_files_list)
        datasets_size=len(camera_files_list)
        print("datasets_size: ",len(camera_files_list))
        
        train_sets=camera_files_list[0:int(self.train_set_proportion*datasets_size)]
        val_sets=camera_files_list[int(self.train_set_proportion*datasets_size):int(self.train_set_proportion*datasets_size)+int(self.validation_set_proportion*datasets_size)]
        test_sets=camera_files_list[int(self.train_set_proportion*datasets_size)+int(self.validation_set_proportion*datasets_size):int(self.train_set_proportion*datasets_size)+int(self.validation_set_proportion*datasets_size)+int(self.test_set_proportion*datasets_size)+1]
        """
        print("train_sets:",train_sets)
        print("val_sets:",val_sets)
        print("test_sets:",test_sets)        
        """
        train_output_path=os.path.join(output_path,"train.txt")
        
        val_output_path=os.path.join(output_path,"val.txt")
        
        test_output_path=os.path.join(output_path,"test.txt")
                
        with open(train_output_path, 'wt') as f:
            print("write file:",train_output_path)
            for index in train_sets:
                if onlyFileName== True:
                    image_name=index
                    label_name=os.path.splitext(index)[0]+".txt"
                    write_col=image_name+" "+label_name+"\n"
                    
                else:
                    
                    image_name=os.path.join(self.image2_path,index)
                    label_name=os.path.join(self.label2_path,os.path.splitext(index)[0]+".txt")
                    write_col=image_name+" "+label_name+"\n"                    
                print(write_col)
                f.write(write_col)  

        with open(val_output_path, 'wt') as f:
            print("write file:",val_output_path)
            for index in val_sets:
                if onlyFileName== True:
                    image_name=index
                    label_name=os.path.splitext(index)[0]+".txt"
                    write_col=image_name+" "+label_name+"\n"
                    
                else:
                    
                    image_name=os.path.join(self.image2_path,index)
                    label_name=os.path.join(self.label2_path,os.path.splitext(index)[0]+".txt")
                    write_col=image_name+" "+label_name+"\n"                    
                print(write_col)
                f.write(write_col)  

        with open(test_output_path, 'wt') as f:
            print("write file:",test_output_path)
            for index in test_sets:
                if onlyFileName== True:
                    image_name=index
                    label_name=os.path.splitext(index)[0]+".txt"
                    write_col=image_name+" "+label_name+"\n"
                    
                else:
                    
                    image_name=os.path.join(self.image2_path,index)
                    label_name=os.path.join(self.label2_path,os.path.splitext(index)[0]+".txt")
                    write_col=image_name+" "+label_name+"\n"                    
                print(write_col)
                f.write(write_col)                  

In [73]:
test_line=['Van']
delete_class=['Trafficcone','Motorcyclist']#Set the list you want to delete
merge_class={'Car':['Van']}#Set the list you want to merge,example 'a':[1, 2, 3],'b':[13, 22, 32],'c':[15, 'sdf']
if test_line[0] in delete_class:
    print("deleted")
for key,value in merge_class.items():
    print(key,value)
    if test_line[0] in value:
        print("replace to ",key)

Car ['Van']
replace to  Car


In [ ]:
#删除label，检查pos和type
#转换
#测试生成label
config_data=read_config('./config/config.yaml')    #read config file get the convert input and output path

dair2kitti=convert_datasets(config_data)    #instantiate the object
dair2kitti.create_path()    #create the subfloder
#base the camera label source, and replace the pos(z) and the size(l,w,h) by the lidar label source.
dair2kitti.label_convert_fix_high(dair2kitti.source_camera_label,dair2kitti.source_velodyne_label,dair2kitti.label2_path)

#You can set the seed to generate the same result. and only output the file name or full path 
#dair2kitti.creat_list() 

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_2/000000.txt
Skip the class Cyclist
write_buffer: Car 0 0 0 960.894714 397.073822 1069.800171 499.614593 1.603673 1.892322 4.216247 38.609590 -4.759066 -0.9021224886694084 -0.023192617826288845 

write_buffer: Car 0 0 0 960.894714 397.073822 1069.800171 499.614593 1.603673 1.892322 4.216247 38.609590 -4.759066 -0.9021224886694084 -0.023192617826288845 
Car 0 3 0 1433.344849 1010.11145 1920.0 1080.0 1.505857 1.826533 4.240506 12.836831 -7.479841 -0.9328727819732601 0.044516711156413806 

Skip the class Trafficcone
Skip the class Trafficcone
write_buffer: Car 0 0 0 960.894714 397.073822 1069.800171 499.614593 1.603673 1.892322 4.216247 38.609590 -4.759066 -0.9021224886694084 -0.023192617826288845 
Car 0 3 0 1433.344849 1010.11145 1920.0 1080.0 1.505857 1.826533 4.240506 12.836831 -7.479841 -0.9328727819732601 0.044516711156413806 
Car 1 3 0 0 228.458496 56.103931 287.786346 1.427104 1.808059 4.289026 70.700904 25.73

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_2/000001.txt
Skip the class Motorcyclist
write_buffer: Car 0 0 0 973.103394 114.435112 997.375184 137.632584 1.490534 1.979685 4.238436 182.935146 -11.787772 -1.1481482683515454 0.030507489913997436 

write_buffer: Car 0 0 0 973.103394 114.435112 997.375184 137.632584 1.490534 1.979685 4.238436 182.935146 -11.787772 -1.1481482683515454 0.030507489913997436 
Car 1 0 0 490.06958 165.804672 542.294617 201.272995 1.392664 1.733107 4.153487 107.222162 14.854510 -1.2352713216296003 3.0625120175699485 

write_buffer: Car 0 0 0 973.103394 114.435112 997.375184 137.632584 1.490534 1.979685 4.238436 182.935146 -11.787772 -1.1481482683515454 0.030507489913997436 
Car 1 0 0 490.06958 165.804672 542.294617 201.272995 1.392664 1.733107 4.153487 107.222162 14.854510 -1.2352713216296003 3.0625120175699485 
Car 0 0 0 936.478149 392.114624 1043.070312 497.858246 1.479081 1.754074 4.288902 39.184599 -4.330972 -0.9203373027137998 -0.

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_2/000002.txt
Skip the class Motorcyclist
Skip the class Cyclist
write_buffer: Car 0 0 0 960.387817 650.730469 1158.447998 864.502381 1.682589 1.934455 4.25546 21.813991 -4.084029 -0.8598796983626942 -0.016544354845634445 

Skip the class Trafficcone
Skip the class Trafficcone
Skip the class Motorcyclist
write_buffer: Car 0 0 0 960.387817 650.730469 1158.447998 864.502381 1.682589 1.934455 4.25546 21.813991 -4.084029 -0.8598796983626942 -0.016544354845634445 
Car 0 0 0 567.795593 145.50119 609.2507320000001 172.18614200000002 1.528996 1.90457 4.242937 129.584453 14.164725 -1.2063053697382058 3.1136507343136817 

write_buffer: Car 0 0 0 960.387817 650.730469 1158.447998 864.502381 1.682589 1.934455 4.25546 21.813991 -4.084029 -0.8598796983626942 -0.016544354845634445 
Car 0 0 0 567.795593 145.50119 609.2507320000001 172.18614200000002 1.528996 1.90457 4.242937 129.584453 14.164725 -1.2063053697382058 3.1136507343136

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_2/000003.txt
Skip the class Trafficcone
write_buffer: Car 0 0 0 534.499329 151.049576 579.106018 182.645493 1.472731 2.092625 4.265708 121.761690 14.920184 -1.2857648204751948 3.0976175619295523 

Skip the class Cyclist
write_buffer: Car 0 0 0 534.499329 151.049576 579.106018 182.645493 1.472731 2.092625 4.265708 121.761690 14.920184 -1.2857648204751948 3.0976175619295523 
Bus 1 0 0 689.554443 88.548515 737.724914 138.815124 3.059433 3.01172 12.006609 173.766268 9.888350 -0.28883193642659055 3.097707339637891 

write_buffer: Car 0 0 0 534.499329 151.049576 579.106018 182.645493 1.472731 2.092625 4.265708 121.761690 14.920184 -1.2857648204751948 3.0976175619295523 
Bus 1 0 0 689.554443 88.548515 737.724914 138.815124 3.059433 3.01172 12.006609 173.766268 9.888350 -0.28883193642659055 3.097707339637891 
Car 0 0 0 888.452087 108.008904 911.347045 126.339547 1.477437 2.264892 4.271339 198.889774 -4.950674 -1.444341569

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_2/000004.txt
Skip the class Motorcyclist
Skip the class Trafficcone
write_buffer: Car 0 0 0 193.157593 743.944092 502.100769 993.0263669999999 1.578242 2.045278 4.534678 18.203885 2.279643 -0.8449088190710707 -0.028134308367199306 

write_buffer: Car 0 0 0 193.157593 743.944092 502.100769 993.0263669999999 1.578242 2.045278 4.534678 18.203885 2.279643 -0.8449088190710707 -0.028134308367199306 
Car 0 0 0 349.899506 329.164978 478.401307 422.35897800000004 1.555267 1.942368 4.37652 45.809579 7.448246 -0.8824400899117588 -2.6731059819130474 

Skip the class Motorcyclist
Skip the class Motorcyclist
write_buffer: Car 0 0 0 193.157593 743.944092 502.100769 993.0263669999999 1.578242 2.045278 4.534678 18.203885 2.279643 -0.8449088190710707 -0.028134308367199306 
Car 0 0 0 349.899506 329.164978 478.401307 422.35897800000004 1.555267 1.942368 4.37652 45.809579 7.448246 -0.8824400899117588 -2.6731059819130474 
Car 2 0 0 872

...

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_2/000428.txt
Skip the class Trafficcone
Skip the class Trafficcone
Skip the class Trafficcone
Skip the class Trafficcone
Skip the class Trafficcone
write_buffer: Car 0 3 0 0 988.206238 293.392365 1080.0 1.439269 1.804141 4.266826 12.746439 3.178790 -0.6234915888930344 -0.14027363004332205 

write_buffer: Car 0 3 0 0 988.206238 293.392365 1080.0 1.439269 1.804141 4.266826 12.746439 3.178790 -0.6234915888930344 -0.14027363004332205 
Pedestrian 0 0 0 1341.940796 298.714447 1379.754883 378.797974 1.657183 0.499321 0.830379 51.348797 -13.909453 -0.928767926961152 1.482760531886608 

Skip the class Trafficcone
write_buffer: Car 0 3 0 0 988.206238 293.392365 1080.0 1.439269 1.804141 4.266826 12.746439 3.178790 -0.6234915888930344 -0.14027363004332205 
Pedestrian 0 0 0 1341.940796 298.714447 1379.754883 378.797974 1.657183 0.499321 0.830379 51.348797 -13.909453 -0.928767926961152 1.482760531886608 
Car 1 0 0 431.663116 47

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_2/000432.txt
Skip the class Trafficcone
Skip the class Trafficcone
Skip the class Trafficcone
Skip the class Trafficcone
write_buffer: Car 0 0 0 89.168159 377.623718 299.909828 481.542053 1.759632 1.800206 4.259164 39.423572 10.121465 -0.8090997331450502 0.9402671138866867 

write_buffer: Car 0 0 0 89.168159 377.623718 299.909828 481.542053 1.759632 1.800206 4.259164 39.423572 10.121465 -0.8090997331450502 0.9402671138866867 
Car 0 0 0 622.589355 136.211197 654.6804189999999 161.636994 1.535192 1.885446 4.274851 187.123318 17.572976 -1.8763399261751115 3.1035673175164495 

Skip the class Trafficcone
write_buffer: Car 0 0 0 89.168159 377.623718 299.909828 481.542053 1.759632 1.800206 4.259164 39.423572 10.121465 -0.8090997331450502 0.9402671138866867 
Car 0 0 0 622.589355 136.211197 654.6804189999999 161.636994 1.535192 1.885446 4.274851 187.123318 17.572976 -1.8763399261751115 3.1035673175164495 
Car 0 0 0 362.373

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_2/000440.txt
Skip the class Trafficcone
write_buffer: Car 0 0 0 1439.978027 341.636292 1669.504394 433.29751600000003 1.528633 1.868182 4.657155 44.344147 -16.409776 -0.94351673347425 1.6047903494220095 

write_buffer: Car 0 0 0 1439.978027 341.636292 1669.504394 433.29751600000003 1.528633 1.868182 4.657155 44.344147 -16.409776 -0.94351673347425 1.6047903494220095 
Truck 0 0 0 75.749695 113.139244 174.288819 166.28779600000001 2.629104 2.647463 7.48676 135.909996 43.134432 0.010118491130603147 -1.6077039774489001 

Skip the class Trafficcone
Skip the class Cyclist
write_buffer: Car 0 0 0 1439.978027 341.636292 1669.504394 433.29751600000003 1.528633 1.868182 4.657155 44.344147 -16.409776 -0.94351673347425 1.6047903494220095 
Truck 0 0 0 75.749695 113.139244 174.288819 166.28779600000001 2.629104 2.647463 7.48676 135.909996 43.134432 0.010118491130603147 -1.6077039774489001 
Car 0 0 0 505.105743 165.366394 567.493

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_2/000441.txt
write_buffer: Car 1 0 0 479.973907 146.911774 528.805175 181.586624 1.463559 1.834394 4.220413 121.482871 17.940568 -1.2974284423562477 -3.0344331031342406 

Skip the class Trafficcone
write_buffer: Car 1 0 0 479.973907 146.911774 528.805175 181.586624 1.463559 1.834394 4.220413 121.482871 17.940568 -1.2974284423562477 -3.0344331031342406 
Car 1 0 0 552.203613 170.511795 596.380859 205.97374000000002 1.544681 1.808881 4.250096 103.490459 11.745732 -0.8453389475556445 3.108284003482319 

write_buffer: Car 1 0 0 479.973907 146.911774 528.805175 181.586624 1.463559 1.834394 4.220413 121.482871 17.940568 -1.2974284423562477 -3.0344331031342406 
Car 1 0 0 552.203613 170.511795 596.380859 205.97374000000002 1.544681 1.808881 4.250096 103.490459 11.745732 -0.8453389475556445 3.108284003482319 
Car 1 0 0 329.056335 207.178741 406.334228 256.935363 1.477907 1.815789 4.351348 80.163270 16.076090 -0.952100285263

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_2/000443.txt
Skip the class Trafficcone
Skip the class Trafficcone
Skip the class Trafficcone
Skip the class Cyclist
write_buffer: Pedestrian 1 0 0 600.932678 272.600586 622.119446 348.93090800000004 1.728611 0.41221 0.478665 55.197526 4.390198 -0.7811908351628141 1.5705172932826919 

write_buffer: Pedestrian 1 0 0 600.932678 272.600586 622.119446 348.93090800000004 1.728611 0.41221 0.478665 55.197526 4.390198 -0.7811908351628141 1.5705172932826919 
Car 0 0 0 495.219208 165.4655 548.1065679999999 202.866501 1.412532 2.076978 4.273797 105.902466 14.566284 -1.5962637118787226 3.0562918387264717 

Skip the class Trafficcone
Skip the class Trafficcone
Skip the class Trafficcone
Skip the class Trafficcone
Skip the class Trafficcone
write_buffer: Pedestrian 1 0 0 600.932678 272.600586 622.119446 348.93090800000004 1.728611 0.41221 0.478665 55.197526 4.390198 -0.7811908351628141 1.5705172932826919 
Car 0 0 0 495.219208 1

In [2]:
#You can select which folders you need to convert by commenting out parts of the code

config_data=read_config('./config/config.yaml')    #read config file get the convert input and output path
dair2kitti=convert_datasets(config_data)    #instantiate the object
dair2kitti.create_path()    #create the subfloders
dair2kitti.calib_convert()    #calib file convert to the kitti format

#camera coordinate label convert, but origin camera label have some issues, so don't use this.
#dair2kitti.label_convert(dair2kitti.source_camera_label,dair2kitti.label2_path)   

#camera coordinate label convert, and fix the camera label issues
#base the camera label source, and replace the pos(z) and the size(l,w,h) by the lidar label source.
dair2kitti.label_convert_fix_high(dair2kitti.source_camera_label,dair2kitti.source_velodyne_label,dair2kitti.label2_path)

#velodyne coordinate label convert
dair2kitti.label_convert(dair2kitti.source_velodyne_label,dair2kitti.label_vel_path)


#Make sure the destination folder does not exist before converting

#copy and rename the camera image floder
dair2kitti.rename_floder(dair2kitti.source_image_path,dair2kitti.image2_path)

#copy and rename the velodyne pcd floder
dair2kitti.rename_floder(dair2kitti.source_velodyne_path,dair2kitti.velodyne_path)
#convert finished

created the path: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib
created the path: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_2
created the path: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000000.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000001.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000002.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000003.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000004.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000005.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000006.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000007.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000008.

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000132.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000133.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000134.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000135.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000136.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000137.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000139.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000140.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000141.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000142.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000143.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000278.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000280.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000281.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000284.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000285.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000287.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000289.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000290.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000294.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000295.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000296.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000443.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000444.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000445.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000446.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000447.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000448.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000449.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000450.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000451.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000452.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000453.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000572.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000573.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000575.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000576.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000577.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000578.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000580.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000581.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000582.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000583.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000584.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/calib/000

...

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009498.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009499.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009500.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009501.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009502.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009504.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009505.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009506.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009507.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009508.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/lab

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009626.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009627.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009628.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009630.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009631.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009633.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009634.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009636.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009637.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009638.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/lab

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009763.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009765.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009766.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009768.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009771.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009772.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009774.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009776.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009777.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009778.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/lab

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009890.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009898.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009899.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009900.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009901.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009902.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009903.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009904.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009905.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/009906.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/lab

write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/010020.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/010021.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/010022.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/010023.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/010026.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/010027.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/010028.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/010029.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/010030.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/label_velodyne/010032.txt
write file: /home/liuchenghua/datasets_nfs/dair_v2x_i/kitti_format/lab